# Model Selection 

The objective of this notebook is to build a very first ent to end Machine Learning model to predict the probability of a patient being discharged on a particular day.

We'll use the dataset generated by the `dataset` job of the ETL folder. 

At this instance, the focus won't be on model performance but rather on understanding the value potential of the available data and the speedness of the solution.

In [1]:
%cd /Users/josefinadallavia/Documents/MIM/Tesis/AML-hospital

/Users/josefinadallavia/Documents/MIM/Tesis/AML-hospital


In [2]:
import warnings
warnings.filterwarnings('ignore')
import os
import pandas as pd
from matplotlib import pyplot as plt   
os.environ['KMP_DUPLICATE_LIB_OK']='True'
from thesis_lib.utils import * 
from thesis_lib.modelling.data import *
from thesis_lib.modelling.model import *


/Users/josefinadallavia/opt/anaconda3/lib/python3.7/importlib/_bootstrap.py:219: RuntimeWarning: numpy.ufunc size changed, may indicate binary incompatibility. Expected 192 from C header, got 216 from PyObject
  return f(*args, **kwds)
/Users/josefinadallavia/opt/anaconda3/lib/python3.7/importlib/_bootstrap.py:219: RuntimeWarning: numpy.ufunc size changed, may indicate binary incompatibility. Expected 192 from C header, got 216 from PyObject
  return f(*args, **kwds)
/Users/josefinadallavia/opt/anaconda3/lib/python3.7/importlib/_bootstrap.py:219: RuntimeWarning: numpy.ufunc size changed, may indicate binary incompatibility. Expected 192 from C header, got 216 from PyObject
  return f(*args, **kwds)


In [3]:
data = Data().load('data/hospital_dataset')
variables = data.get_variables_dict()
data.get_stats()

Loading dataset:  hospital_train_data.parquet
Loading dataset:  hospital_val_data.parquet
Loading dataset:  hospital_test_data.parquet


dataset_type         train         val        test
n_observations      319150       33482       33309
relative_size      0.82694   0.0867542   0.0863059
n_cols                  71          71          71
positives            42697        4555        4507
negatives           276453       28927       28802
positive_prop     0.133783    0.136043    0.135309
negative_prop     0.866217    0.863957    0.864691
min_date        2017-01-01  2018-11-11  2018-11-11
max_date        2018-11-10  2019-11-11  2019-11-11

In [4]:
sequence_features = ['labos_studies_names','sectors_names','images_study_types','surgeries_types',
                    'surgeries_injury_condition','surgeries_post_surgery_condition','surgeries_anesthesia_types']

In [5]:
text_features = ['administrative_diagnosis','presumptive_dianogsis','images_studies_names',
                'surgeries_actual']

In [6]:
text_features = [ 'administrative_diagnosis','presumptive_dianogsis','images_studies_names',
                'surgeries_actual' ,            
    'labos_studies_names','sectors_names','images_study_types','surgeries_types',
                    'surgeries_injury_condition','surgeries_post_surgery_condition','surgeries_anesthesia_types']

In [7]:
categorical_features = ['date_weekday',
 'request_origin',
 'origin',
 'entity_group',
 'gender',
 'request_sector',
 'insurance_entity',
 'admission_sector',
 'emergency_service',
 'isolation',
 'ARM_TEP',
 'CEC_TEP',
 'request_sector',
 'date_weekday',
 'admission_weekday',
 'date_month',
 'admission_month']

In [8]:
numerical_features = ['PIM2TEP',
 'emergency_service',
 'high_risk_TEP',
 'hosp_day_number',
 'images_count',
 'images_cumulative',
 'images_emergencies',
 'images_requester_roles_count',
 'images_requesters_count',
 'images_study_types_count',
 'labos_count',
 'labos_cumulative',
 'labos_emergencies',
 'labos_requester_roles_count',
 'labos_requesters_count',
 'labos_set_count',
 'labos_set_cumulative',
 'low_risk_TEP',
 'new_born_gestation_age',
 'new_born_weight',
 'patient_age',
 'sectors_count',
 'surgeries_count',
 'surgeries_cumulative',
 'surgeries_post_surgery_duration',
 'surgeries_pre_surgery_duration',
 'surgeries_prep_duration',
 'surgeries_services_count',
 'surgeries_surgery_delay',
 'surgeries_surgery_duration',
 'surgeries_types_count']

### All features

In [9]:
model_params = {'classifier': 'lgbm',
               'accepts_sparse': True,
                'categorical_features' : categorical_features ,
                'numerical_features' : numerical_features,
               'text_features': text_features,
                #'sequence_features':sequence_features
               }

In [10]:
lgbm_comb_features = Model(**model_params)
lgbm_comb_features.transform(data)

Fitting pipeline...
	 Preprocessing data
	 Preprocessing data
	 Encoding Categorical Features with OneHotEncoding
	 Preprocessing data
	 Preprocessing data
	 Preprocessing data
	 Preprocessing data
	 Preprocessing data
	 Preprocessing data
	 Preprocessing data
	 Preprocessing data
	 Preprocessing data
	 Preprocessing data
	 Preprocessing data
Transforming data...
	 Transforming numerical features
	 Preprocessing data
	 Transforming categorical features
	 Preprocessing data
	 Transforming text features
	 Preprocessing data
	 Transforming text features with TF-IDF embeddings
	 Transforming text features
	 Preprocessing data
	 Transforming text features with TF-IDF embeddings
	 Transforming text features
	 Preprocessing data
	 Transforming text features with TF-IDF embeddings
	 Transforming text features
	 Preprocessing data
	 Transforming text features with TF-IDF embeddings
	 Transforming text features
	 Preprocessing data
	 Transforming text features with TF-IDF embeddings
	 Transformi

In [11]:
lgbm_comb_features.n_features

20089

In [12]:
%%time
#lgbm_comb_features.fit_classifier()

CPU times: user 4 µs, sys: 0 ns, total: 4 µs
Wall time: 27.9 µs


In [13]:
#lgbm_comb_features.get_performance_metrics()

### Fine tuning

### Objective function

In [12]:
import lightgbm as lgb
import flatdict
from hyperopt import STATUS_OK

N_FOLDS = 3

# Create the dataset
train_set = lgb.Dataset(lgbm_comb_features.X_train,label=lgbm_comb_features.y_train)

def objective(params, n_folds = N_FOLDS):
    """Objective function for Gradient Boosting Machine Hyperparameter Tuning"""
    flatten_params = flatdict.FlatDict(params)
    parameters ={param_name: flatten_params[param_name] for param_name in flatten_params}
    
    
    # Perform n_fold cross validation with hyperparameters
    # Use early stopping and evalute based on ROC AUC
    cv_results = lgb.cv(params = parameters, train_set = train_set,
                        nfold = n_folds,
                        num_boost_round=parameters.get('num_boost_round',100),
                        early_stopping_rounds = 100, metrics = 'auc', seed = 2020,
                        verbose_eval=True)
  
    # Extract the best score
    best_score = max(cv_results['auc-mean'])
    
    # Loss must be minimized
    loss = 1 - best_score
    
    # Dictionary with information for evaluation
    return {'loss': loss, 'params': params, 'status': STATUS_OK}

### Domain space

In [13]:
from hyperopt import hp

space_lgbm = {
    'objective': hp.choice('objective', ['binary']),
    'boosting_type': 'gbdt', 
    'subsample': hp.uniform('gdbt_subsample', 0.5, 1),
    'max_depth': hp.quniform('max_depth', 5, 30,1),
    'learning_rate': hp.loguniform('learning_rate', np.log(0.001), np.log(0.1)),
    'num_boost_round': hp.choice('num_iterations', [100,150,200,300,500])}

In [14]:
import hyperopt.pyll.stochastic 

### Optimization algorithm

In [15]:
from hyperopt import tpe
# Algorithm
tpe_algorithm = tpe.suggest

### Result history

In [16]:
from hyperopt import Trials
# Trials object to track progress
bayes_trials_lgbm = Trials()

### Optimization

In [17]:
from hyperopt import fmin

MAX_EVALS = 200

# Optimize
best = fmin(fn = objective, space = space_lgbm, algo = tpe.suggest, 
            max_evals = MAX_EVALS, trials = bayes_trials_lgbm)

  0%|          | 0/200 [00:00<?, ?trial/s, best loss=?]

/Users/josefinadallavia/opt/anaconda3/lib/python3.7/site-packages/lightgbm/engine.py:503: UserWarning: Found `num_boost_round` in params. Will use it instead of argument
  warnings.warn("Found `{}` in params. Will use it instead of argument".format(alias))



[1]	cv_agg's auc: 0.79071 + 0.00162647                 
[2]	cv_agg's auc: 0.791378 + 0.00210341                
[3]	cv_agg's auc: 0.791395 + 0.00205782                
[4]	cv_agg's auc: 0.791402 + 0.00210476                
[5]	cv_agg's auc: 0.791452 + 0.00206964                
[6]	cv_agg's auc: 0.791544 + 0.00207582                
[7]	cv_agg's auc: 0.791545 + 0.00206772                
[8]	cv_agg's auc: 0.791548 + 0.00208056                
[9]	cv_agg's auc: 0.791559 + 0.00208463                
[10]	cv_agg's auc: 0.791595 + 0.0020385                
[11]	cv_agg's auc: 0.791667 + 0.00201019               
[12]	cv_agg's auc: 0.791811 + 0.00184969               
[13]	cv_agg's auc: 0.791809 + 0.00189083               
[14]	cv_agg's auc: 0.791831 + 0.00188303               
[15]	cv_agg's auc: 0.791821 + 0.00187964               
[16]	cv_agg's auc: 0.792194 + 0.00231453               
[17]	cv_agg's auc: 0.79222 + 0.00231019                
[18]	cv_agg's auc: 0.794354 + 0.002686          

[147]	cv_agg's auc: 0.811584 + 0.00247347              
[148]	cv_agg's auc: 0.811623 + 0.00248196              
[149]	cv_agg's auc: 0.811649 + 0.00247765              
[150]	cv_agg's auc: 0.811686 + 0.00248383              
[151]	cv_agg's auc: 0.811709 + 0.00249833              
[152]	cv_agg's auc: 0.811746 + 0.00248795              
[153]	cv_agg's auc: 0.811747 + 0.00249832              
[154]	cv_agg's auc: 0.811852 + 0.00246939              
[155]	cv_agg's auc: 0.811926 + 0.00244391              
[156]	cv_agg's auc: 0.811914 + 0.00246836              
[157]	cv_agg's auc: 0.811977 + 0.00244532              
[158]	cv_agg's auc: 0.812034 + 0.00241699              
[159]	cv_agg's auc: 0.812173 + 0.00233837              
[160]	cv_agg's auc: 0.812256 + 0.00235813              
[161]	cv_agg's auc: 0.812338 + 0.00234713              
[162]	cv_agg's auc: 0.812382 + 0.00234829              
[163]	cv_agg's auc: 0.812438 + 0.00230886              
[164]	cv_agg's auc: 0.812504 + 0.00234754       

/Users/josefinadallavia/opt/anaconda3/lib/python3.7/site-packages/lightgbm/engine.py:503: UserWarning: Found `num_boost_round` in params. Will use it instead of argument
  warnings.warn("Found `{}` in params. Will use it instead of argument".format(alias))



...

[93]	cv_agg's auc: 0.840416 + 0.00166321                                                
[94]	cv_agg's auc: 0.840522 + 0.00169952                                                
[95]	cv_agg's auc: 0.840638 + 0.00167137                                                
[96]	cv_agg's auc: 0.840705 + 0.00167049                                                
[97]	cv_agg's auc: 0.840807 + 0.0016743                                                 
[98]	cv_agg's auc: 0.840886 + 0.00167932                                                
[99]	cv_agg's auc: 0.840984 + 0.00169624                                                
[100]	cv_agg's auc: 0.841061 + 0.00170963                                               
[101]	cv_agg's auc: 0.841119 + 0.00170083                                               
[102]	cv_agg's auc: 0.841203 + 0.00167431                                               
[103]	cv_agg's auc: 0.841296 + 0.00167597                                               
[104]	cv_agg's auc: 0

[185]	cv_agg's auc: 0.845113 + 0.00171592                                               
[186]	cv_agg's auc: 0.845144 + 0.0017071                                                
[187]	cv_agg's auc: 0.845163 + 0.00170059                                               
[188]	cv_agg's auc: 0.8452 + 0.00170731                                                 
[189]	cv_agg's auc: 0.845217 + 0.00170165                                               
[190]	cv_agg's auc: 0.845241 + 0.00168703                                               
[191]	cv_agg's auc: 0.845321 + 0.00165191                                               
[192]	cv_agg's auc: 0.845339 + 0.00164914                                               
[193]	cv_agg's auc: 0.845363 + 0.00165155                                               
[194]	cv_agg's auc: 0.845396 + 0.00165352                                               
[195]	cv_agg's auc: 0.845459 + 0.00166147                                               
[196]	cv_agg's auc: 0

[277]	cv_agg's auc: 0.847105 + 0.00157383                                               
[278]	cv_agg's auc: 0.847151 + 0.00157322                                               
[279]	cv_agg's auc: 0.847166 + 0.00155931                                               
[280]	cv_agg's auc: 0.84718 + 0.00155206                                                
[281]	cv_agg's auc: 0.847193 + 0.00155844                                               
[282]	cv_agg's auc: 0.847208 + 0.00156242                                               
[283]	cv_agg's auc: 0.847229 + 0.00157819                                               
[284]	cv_agg's auc: 0.847239 + 0.00158633                                               
[285]	cv_agg's auc: 0.84725 + 0.0016011                                                 
[286]	cv_agg's auc: 0.847253 + 0.00159693                                               
[287]	cv_agg's auc: 0.847277 + 0.0015871                                                
[288]	cv_agg's auc: 0

[369]	cv_agg's auc: 0.848322 + 0.00150975                                               
[370]	cv_agg's auc: 0.84832 + 0.00150394                                                
[371]	cv_agg's auc: 0.848327 + 0.00150828                                               
[372]	cv_agg's auc: 0.848338 + 0.001511                                                 
[373]	cv_agg's auc: 0.848365 + 0.00147827                                               
[374]	cv_agg's auc: 0.848375 + 0.00149108                                               
[375]	cv_agg's auc: 0.848382 + 0.00148166                                               
[376]	cv_agg's auc: 0.848384 + 0.00148371                                               
[377]	cv_agg's auc: 0.848408 + 0.00148193                                               
[378]	cv_agg's auc: 0.848415 + 0.00148087                                               
[379]	cv_agg's auc: 0.848419 + 0.00148426                                               
[380]	cv_agg's auc: 0

[461]	cv_agg's auc: 0.848995 + 0.00149347                                               
[462]	cv_agg's auc: 0.849 + 0.0014938                                                   
[463]	cv_agg's auc: 0.849005 + 0.0014975                                                
[464]	cv_agg's auc: 0.849005 + 0.00149731                                               
[465]	cv_agg's auc: 0.84901 + 0.0014959                                                 
[466]	cv_agg's auc: 0.849023 + 0.00150786                                               
[467]	cv_agg's auc: 0.849044 + 0.00151268                                               
[468]	cv_agg's auc: 0.84906 + 0.00148628                                                
[469]	cv_agg's auc: 0.849074 + 0.00147841                                               
[470]	cv_agg's auc: 0.849083 + 0.00147775                                               
[471]	cv_agg's auc: 0.84908 + 0.00148412                                                
[472]	cv_agg's auc: 0

In [18]:
!pip show hyperopt

Name: hyperopt
Version: 0.2.4
Summary: Distributed Asynchronous Hyperparameter Optimization
Home-page: http://hyperopt.github.com/hyperopt/
Author: James Bergstra
Author-email: james.bergstra@gmail.com
License: BSD
Location: /Users/josefinadallavia/opt/anaconda3/lib/python3.7/site-packages
Requires: cloudpickle, numpy, networkx, future, scipy, tqdm, six
Required-by: 


In [19]:
bayes_trials_lgbm.results

[{'loss': 0.18564319778060012,
  'params': {'boosting_type': 'gbdt',
   'learning_rate': 0.002412328418503243,
   'max_depth': 7,
   'num_boost_round': 200,
   'objective': 'binary',
   'subsample': 0.8248634437312539},
  'status': 'ok'},
 {'loss': 0.16676997609829558,
  'params': {'boosting_type': 'gbdt',
   'learning_rate': 0.011443856982384162,
   'max_depth': 10,
   'num_boost_round': 200,
   'objective': 'binary',
   'subsample': 0.7744044455295506},
  'status': 'ok'},
 {'loss': 0.16886633760388337,
  'params': {'boosting_type': 'gbdt',
   'learning_rate': 0.019432369814710315,
   'max_depth': 29,
   'num_boost_round': 100,
   'objective': 'binary',
   'subsample': 0.7086884705341783},
  'status': 'ok'},
 {'loss': 0.15985155100962822,
  'params': {'boosting_type': 'gbdt',
   'learning_rate': 0.03961270340395006,
   'max_depth': 18,
   'num_boost_round': 100,
   'objective': 'binary',
   'subsample': 0.564872006280588},
  'status': 'ok'},
 {'loss': 0.195074240389582,
  'params': {'

In [20]:
gbdt_results = []
for result in bayes_trials_lgbm.results:
    flatten_results = flatdict.FlatDict(result)
    dict_results = {key: flatten_results[key] for key in flatten_results}
    gbdt_results.append(dict_results)

In [21]:
best

{'gdbt_subsample': 0.7150456664683804,
 'learning_rate': 0.06193103006755226,
 'max_depth': 20.0,
 'num_iterations': 4,
 'objective': 0}

In [22]:
filename = '/Users/josefinadallavia/Documents/MIM/Tesis/AML-hospital/experiments/gdbt_auto_ml_results.csv'

In [23]:
import csv
fieldnames = list(gbdt_results[0].keys())
    
with open(filename, 'w') as output_file:
    writer = csv.DictWriter(output_file, fieldnames=fieldnames)
    writer.writeheader()
    writer.writerows(gbdt_results)